In [1]:
import pandas as pd
import re

pd.options.display.max_columns = 50
pd.options.display.max_rows = 50

In [2]:
contracts = pd.read_csv('../data/contracts.csv', low_memory=False)

categories = pd.read_csv('../data/REVISED_economic_object_codes_to_category.csv', low_memory=False)


contracts.head()

reference_number procurement_id  \
0  C-2021-2022-Q3-00001       P2100021   
1  C-2021-2022-Q3-00002       P2200003   
2  C-2021-2022-Q3-00003       P2200004   
3  C-2021-2022-Q3-00004       P2200016   
4  C-2021-2022-Q3-00005       P2200016   

                                  vendor_name vendor_postal_code buyer_name  \
0                     MacKinnon-Charlton Ltd.                K1G        NaN   
1                                         NaN                NaN        NaN   
2  The Right Door Consulting & Solutions Inc.                K2P        NaN   
3                       Senez Consulting Ltd.                V4L        NaN   
4                       Senez Consulting Ltd.                V4L        NaN   

  contract_date economic_object_code  \
0    2021-03-09                  414   
1    2021-10-14                 0494   
2    2021-06-21                 0473   
3    2021-10-12                 0492   
4    2021-10-12                 0492   

                                      description_en  \
0                           Human resources services   
1                       0493 Interpretation services   
2  0473 Information Technology and Telecommunicat...   
3                            0492 Research Contracts   
4                            0492 Research Contracts   

                                      description_fr contract_period_start  \
0                     Services de ressources humaine            2021-03-03   
1                     0493 Services d'interprètation            2021-10-14   
2  0473 Experts-conseils en technologie de l'info...            2021-06-03   
3                         0492 Contrats de recherche            2021-09-15   
4                         0492 Contrats de recherche            2021-09-15   

  delivery_date  contract_value  original_value  amendment_value  \
0    2022-03-31        40000.00         28250.0         11750.00   
1    2026-09-30       750000.00        750000.0              NaN   
2    2022-03-31        59189.40         39663.0         19526.40   
3    2022-03-31       126472.50        126472.5              NaN   
4    2022-03-31       189708.75        126472.5         63236.25   

                          comments_en  \
0           Work description services   
1  Supply arrangement (SLIAO and CHS)   
2                Creation of database   
3                 Standards research    
4                 Standards research    

                                         comments_fr additional_comments_en  \
0                 Services de description de travail                    NaN   
1  Arrangement en matiere d'approvisionnement (SL...                    NaN   
2                        creation de base de donnees                    NaN   
3                                Recherche de normes                    NaN   
4                                Recherche de normes                    NaN   

  additional_comments_fr agreement_type_code trade_agreement land_claims  \
0                    NaN                   0             NaN         NaN   
1                    NaN                   0             NaN         NaN   
2                    NaN                   0             NaN         NaN   
3                    NaN                   0             NaN         NaN   
4                    NaN                   0             NaN         NaN   

  commodity_type commodity_code country_of_vendor solicitation_procedure  \
0              S         R019BF                CA                     TN   
1              S          R109B                CA                     OB   
2              S          D302A                CA                     TN   
3              S          T000B                CA                     TN   
4              S          T000B                CA                     TN   

  limited_tendering_reason trade_agreement_exceptions aboriginal_business  \
0                       00                         00                 NaN   
1                       00       

In [3]:
contracts = contracts.drop(['vendor_postal_code', 'description_fr', 'comments_fr', 'additional_comments_fr', 'vendor_postal_code'], axis=1)
contracts

reference_number procurement_id  \
0       C-2021-2022-Q3-00001       P2100021   
1       C-2021-2022-Q3-00002       P2200003   
2       C-2021-2022-Q3-00003       P2200004   
3       C-2021-2022-Q3-00004       P2200016   
4       C-2021-2022-Q3-00005       P2200016   
...                      ...            ...   
876255  C-2019-2020-Q2-00020       P2000102   
876256  C-2019-2020-Q2-00021       P2000103   
876257  C-2019-2020-Q3-00001       P2000003   
876258  C-2019-2020-Q3-00006       P2000108   
876259  C-2019-2020-Q3-00023       P2000157   

                                       vendor_name buyer_name contract_date  \
0                          MacKinnon-Charlton Ltd.        NaN    2021-03-09   
1                                              NaN        NaN    2021-10-14   
2       The Right Door Consulting & Solutions Inc.        NaN    2021-06-21   
3                            Senez Consulting Ltd.        NaN    2021-10-12   
4                            Senez Consulting Ltd.        NaN    2021-10-12   
...                                            ...        ...           ...   
876255              Asokan Business Interiors Inc.        NaN    2019-09-25   
876256                         Global Total Office        NaN    2019-09-25   
876257                              CNW Group Ltd.        NaN    2019-03-20   
876258                                     MNP LLP        NaN    2019-10-04   
876259                   WATERSMART SOLUTIONS LTD.        NaN    2019-12-09   

       economic_object_code  \
0                       414   
1                      0494   
2                      0473   
3                      0492   
4                      0492   
...                     ...   
876255                 1231   
876256                 1231   
876257                 0351   
876258                 0401   
876259                 0491   

                                           description_en  \
0                                Human resources services   
1                            0493 Interpretation services   
2       0473 Information Technology and Telecommunicat...   
3                                 0492 Research Contracts   
4                                 0492 Research Contracts   
...                                                   ...   
876255      Office furniture and furnishings, incl. Parts   
876256      Office furniture and furnishings, incl. Parts   
876257  Communications professional services not elsew...   
876258                      Accounting and audit services   
876259  Management consulting, except other depts or p...   

       contract_period_start delivery_date  contract_value  original_value  \
0                 2021-03-03    2022-03-31        40000.00        28250.00   
1                 2021-10-14    2026-09-30       750000.00       750000.00   
2                 2021-06-03    2022-03-31        59189.40        39663.00   
3                 2021-09-15    2022-03-31       126472.50       126472.50   
4                 2021-09-15    2022-03-31       189708.75       126472.50   
...                      ...           ...             ...             ...   
876255            2019-09-25    2019-10-21        17091.25        17091.25   
876256            2019-09-25    2019-10-21        24617.56        24617.56   
876257            2019-04-01    2020-03-31        12995.00         9605.00   
876258            2019-10-04    2020-01-31        18687.55        18687.55   
876259            2019-12-09    2020-03-31       100000.00       100000.00   

        amendment_value                         comments_en  \
0              11750.00           Work description services   
1                   NaN  Supply arrangement (SLIAO and CHS)   
2              19526.40                Creation of database   
3                   NaN                 Standards research    
4              63236.25                 Standards research    
...                 ...                                 ...   
876255        

In [4]:
# normalise object codes in contracts.csv and economic_object_codes_to_category.csv

def normalise_codes(eco_code):
    eco_code = str(eco_code)
    if pd.isna(eco_code) == False and len(eco_code) == 3 and eco_code.isdigit():
        if eco_code[0] != '0':
            eco_code = "0" + eco_code
            return eco_code
    else:
        return eco_code

contracts['economic_object_code'] = contracts['economic_object_code'].apply(normalise_codes)
categories['economic_object_code'] = categories['economic_object_code'].apply(normalise_codes)

## Creating table of EOCs which exist in `contracts.csv` for manual categorization

In [5]:
# TEMP COPY OF CONTRACTS DF FOR EXPERIMENTING BELOW
temp_contracts = contracts
temp_cats = categories

In [6]:
def clean_desc(desc):
    cleaned = ''.join([i for i in desc if i.isalpha()]).lower()
    return cleaned

temp_cats['example_description_en'] = temp_cats['example_description_en'].apply(clean_desc)


In [7]:
for row_index, eco_code in enumerate(temp_contracts['economic_object_code']):
    # check for rows with no EOC or incorrectly formatted EOCs
    if pd.isna(eco_code) or eco_code[0].isdigit() == False:
        if pd.isna(temp_contracts.loc[row_index]['description_en']) == False:
            split_desc = str.split(temp_contracts.loc[row_index]['description_en'])
            for str_index, s in enumerate(split_desc):
                if s.isdigit():
                    if s[0] == '0':
                        # easy match: if number begins with 0 then it can be presumed to be an object code
                        temp_contracts.loc[row_index, 'economic_object_code'] = s
                    elif len(s) >= 3 and str_index == 0:
                        # harder match: what about the 4 digit codes or the ones that don't follow the correct format?
                        # solution: if number is >= 3 digits in length and the number is at index 0, then match number to categories 
                        s = normalise_codes(s)
                        temp_contracts.loc[row_index, 'economic_object_code'] = s
                else:
                    # last EOC check: match descriptions

                    cleanedDesc = clean_desc(temp_contracts.loc[row_index]['description_en'])
                    print(cleanedDesc)
                    getEOC = temp_cats[temp_cats['example_description_en'] == cleanedDesc] 
                    print(getEOC['economic_object_code'].values)
                    print('--------------------------------------------------')

                        
        # else:
        #     temp_contracts.loc[row_index, 'economic_object_code'] = 'Unspecified'


laboratoryequipment
[]
--------------------------------------------------
laboratoryequipment
[]
--------------------------------------------------
fixedwingaircraft
[]
--------------------------------------------------
fixedwingaircraft
[]
--------------------------------------------------
fixedwingaircraft
[]
--------------------------------------------------
cctvequipment
[]
--------------------------------------------------
cctvequipment
[]
--------------------------------------------------
cctvequipment
[]
--------------------------------------------------
cctvequipment
[]
--------------------------------------------------
signs
[]
--------------------------------------------------
cctvequipment
[]
--------------------------------------------------
cctvequipment
[]
--------------------------------------------------
shipandmarine
[]
--------------------------------------------------
shipandmarine
[]
--------------------------------------------------
shipandmarine
[]
---------------

## Code for Categorisation

In [ ]:
temp_contracts = temp_contracts.sort_values(by='economic_object_code')
temp_contracts.to_csv('check.csv')

In [ ]:
# categorise each row 
data_gov_category = []

# TEMP check for unclassifed ECs
unclassified = {}

for i, eco_code in enumerate(temp_contracts['economic_object_code']):
    if pd.isna(eco_code) == False:
        tempdf = temp_contracts.iloc[[i]]
        extract_row = categories[categories['economic_object_code'].str.contains(eco_code)]
        category = extract_row['category'].values
        if len(category) > 0:
            data_gov_category.append(category[0])
        else:
            getDesc = tempdf['description_en'].values
            unclassified[eco_code] = getDesc[0]

unclassified = pd.DataFrame.from_dict(unclassified, orient='index')